In [ ]:
from DATA225utils import make_connection, dataframe_query

# ZAGI Sales

In [ ]:
conn = make_connection(config_file = 'ZAGI-Sales.ini')
cursor = conn.cursor()

In [ ]:
_, df = dataframe_query(conn, "SELECT * FROM product")
df

In [ ]:
_, df = dataframe_query(conn, "SELECT * FROM sold_via")
df

In [ ]:
cursor.execute("DROP VIEW IF EXISTS products_more_than_3_sold")

sql = ( """
        CREATE VIEW products_more_than_3_sold AS
        SELECT product_id, product_name, product_price
        FROM product
        WHERE product_id IN (SELECT product_id
                             FROM sold_via
                             GROUP BY product_id
                             HAVING SUM(no_of_items) > 3)
        """
      )

cursor.execute(sql)

In [ ]:
_, df = dataframe_query(conn, 'SELECT * FROM products_more_than_3_sold')

df

In [ ]:
cursor.execute("DROP VIEW IF EXISTS products_in_multiple_trnsc")

sql = ( """
        CREATE VIEW products_in_multiple_trnsc AS
        SELECT product_id, product_name, product_price
        FROM product
        WHERE product_id IN (SELECT product_id
                             FROM sold_via
                             GROUP BY product_id
                             HAVING COUNT(*) > 1);
        """
      )

cursor.execute(sql)

In [ ]:
_, df = dataframe_query(conn, 'SELECT * FROM products_in_multiple_trnsc')

df

In [ ]:
cursor.close()
conn.close()

# School

In [ ]:
conn = make_connection('school.ini')
cursor = conn.cursor()

In [ ]:
cursor.execute("DROP VIEW IF EXISTS tim_novak_class_codes")

sql = ( """
        CREATE VIEW tim_novak_class_codes AS
        SELECT code 
        FROM student, class, takes 
        WHERE last = 'Novak' 
        AND first = 'Tim' 
        AND id = student_id 
        AND code = class_code    
        """
      )

cursor.execute(sql)

In [ ]:
_, df = dataframe_query(conn, 'SELECT * FROM tim_novak_class_codes')

df

In [ ]:
_, df = dataframe_query(conn,
    """
    SELECT DISTINCT id, first, last
    FROM student, class, takes
    WHERE id = student_id 
    AND code = class_code 
    AND last != 'Novak' 
    AND first != 'Tim' 
    AND class_code IN (
        SELECT * FROM tim_novak_class_codes
    )    
    ORDER BY last
    """
)

display(df)

In [ ]:
cursor.close()
conn.close()